In [1]:
import os
import tempfile
import scanpy as sc
import seaborn as sns
import anndata as ad
import pandas as pd
import warnings 
from scipy.stats import median_abs_deviation
import numpy as np

warnings.simplefilter(action='ignore', category=Warning)


In [80]:
adata = sc.read("adata_files/combined_filtered.h5ad")

In [81]:
groups = adata.obs.groupby("sample").indices

In [82]:
adatas_filtered = {}
for sample_name, inds in groups.items():
    adatas_filtered[sample_name] = adata[inds]

In [20]:
import logging

import anndata2ri
import rpy2.rinterface_lib.callbacks as rcb
import rpy2.robjects as ro

rcb.logger.setLevel(logging.ERROR)

%load_ext rpy2.ipython
anndata2ri.set_ipython_converter()

The rpy2.ipython extension is already loaded. To reload it, use:
  %reload_ext rpy2.ipython


In [21]:
%%R
library(SoupX)

In [114]:
for sam, adt in adatas_filtered.items():
    print(sam)
    adata_pp = adt.copy()
    sc.pp.filter_genes(adata_pp, min_counts=1)
    sc.pp.filter_genes(adata_pp, min_cells=3)
    sc.pp.normalize_per_cell(adata_pp)
    sc.pp.log1p(adata_pp)
    sc.pp.scale(adata_pp, max_value=10)
    sc.pp.pca(adata_pp)
    sc.pp.neighbors(adata_pp)
    sc.tl.leiden(adata_pp, key_added="soupx_groups")
    soupx_groups = adata_pp.obs["soupx_groups"]
    del adata_pp
    
    cells = adt.obs_names
    genes = adt.var_names
    data = adt.X.T
    
    # load raw data
    raw_file = "adata_files/raw/" + sam + ".h5ad"
    adt_raw = sc.read(raw_file)
    adt_raw.var_names_make_unique()
    data_tod = adt_raw.X.T
    del adt_raw

    #### R parts start #####
    ########################
    %R -i data -i data_tod -i genes -i cells -i soupx_groups 
    
    # specify row and column names of data
    %R rownames(data) = genes
    %R colnames(data) = cells
    %R rownames(data_tod) = genes

    # ensure correct sparse format for table of counts and table of droplets
    %R data <- as(data, "sparseMatrix")
    %R data_tod <- as(data_tod, "sparseMatrix")

    # Generate SoupChannel Object for SoupX 
    %R sc = SoupChannel(data_tod, data)
    
    # Set cluster information in SoupChannel
    %R sc = setClusters(sc, soupx_groups)
    
    # Estimate contamination fraction
    %R sc  = autoEstCont(sc, doPlot=FALSE)
    
    # Infer corrected table of counts and rount to integer
    %R -o out out = adjustCounts(sc, roundToInt = TRUE)
    
    #### R parts end #####
    ########################
    
    adt.layers["counts"] = adt.X
    adt.layers["soupX_counts"] = out.T
    adt.X = adt.layers["soupX_counts"]
    adt.obs["soupX_contamination"] = (
        (adt.layers["counts"].sum(axis=1) - adt.layers["soupX_counts"].sum(axis=1)
        ) / adt.layers["counts"].sum(axis=1))
                                                      

TREG002_ASTRL


27 genes passed tf-idf cut-off and 16 soup quantile filter.  Taking the top 16.
Using 64 independent estimates of rho.
Estimated global rho of 0.03


Expanding counts from 6 clusters to 1134 cells.
In addition: Warning message:
In sparseMatrix(i = out@i[w] + 1, j = out@j[w] + 1, x = out@x[w],  :
  'giveCsparse' is deprecated; setting repr="T" for you


TREG002_PBMC


623 genes passed tf-idf cut-off and 217 soup quantile filter.  Taking the top 100.
Using 1073 independent estimates of rho.
Estimated global rho of 0.01


...

190 genes passed tf-idf cut-off and 106 soup quantile filter.  Taking the top 100.
Using 983 independent estimates of rho.
Estimated global rho of 0.02


Expanding counts from 13 clusters to 3829 cells.
In addition: Warning message:
In sparseMatrix(i = out@i[w] + 1, j = out@j[w] + 1, x = out@x[w],  :
  'giveCsparse' is deprecated; setting repr="T" for you


TREG072_PBMC


724 genes passed tf-idf cut-off and 360 soup quantile filter.  Taking the top 100.
Using 1075 independent estimates of rho.
Estimated global rho of 0.03


Expanding counts from 14 clusters to 2802 cells.
In addition: Warning message:
In sparseMatrix(i = out@i[w] + 1, j = out@j[w] + 1, x = out@x[w],  :
  'giveCsparse' is deprecated; setting repr="T" for you


In [115]:
for sam, adt in adatas_filtered.items():
    h5_file = os.path.join("adata_files/soupx/", sam + ".h5ad")
    adt.write(h5_file)